## Informativo de Operação Irregular

![Painel](painel_tempo_real.png)

**Perguntas-chave**

- Quais linhas **precisam** ser desviadas?
  - Linhas afetadas (priorização: quantos passageiros carregam? quantos onibus estão operacionais?)
- Para **onde** pode ser desviado?
  - Onde estão os alagamentos?
  - Onde tem menos trânsito?

---

**Status da Operação:**

- Consórcio
- Linha
- Status: Crítica, Atenção, Regular
- Índice de operação (# veiculos atual / historico)
- Índice de alagamento ()

**O que é um veículo operante?**

- Movimentação nos ultimos 20 minutos

In [6]:
# ! pwd

In [7]:
from zipfile import ZipFile
import pandas as pd
import geopandas as gpd
from folium.plugins import HeatMap
import folium
from shapely.geometry import LineString

with ZipFile("../src/data/gtfs_2024-01-15_2024-01-31.zip") as myzip:

    shapes = pd.read_csv(myzip.open("shapes.txt"), dtype={
                'shape_id': 'str', 
                'shape_pt_lat': 'float', 
                'shape_pt_lon': 'float',  
                'shape_pt_sequence': 'Int64', 
                'shape_dist_traveled': 'float',
            })

    shapes = gpd.GeoDataFrame(shapes,
        geometry=gpd.points_from_xy(shapes.shape_pt_lon, shapes.shape_pt_lat)
    ).set_crs(epsg=4326)

# Sort shapes by shape_pt_sequence
shapes.sort_values(['shape_id','shape_pt_sequence'], inplace=True)
shapes = (
    shapes[["shape_id", "shape_pt_lat", "shape_pt_lon"]]
    .groupby("shape_id")
    .agg(list)
    .apply(lambda x: LineString(zip(x[1], x[0])), axis=1)
)

shapes = gpd.GeoDataFrame(
    data=shapes.index,
    geometry = shapes.values,
    crs=4326
)
shapes['shape_id'] = shapes.shape_id.astype(str)

ocorrencias = pd.read_csv("../src/data/ocorrencias_alagamento_2022-01-01_2024-01-18.csv")

t = ocorrencias.groupby(["latitude", "longitude"]).gravidade.count().reset_index()

m = folium.Map(location=[-22.917690, -43.413861], zoom_start=11)

HeatMap(t, min_opacity=0.4, blur = 18).add_to(folium.FeatureGroup(name='Heat Map').add_to(m))
folium.GeoJson(shapes['geometry'], color='blue', weight=2.5, opacity=1).add_to(m)

folium.TileLayer('cartodbpositron').add_to(m)
folium.LayerControl().add_to(m)

m

/Users/fernandascovino/Projects/prefeitura-rio/monitoramento-operacao/.venv/lib/python3.9/site-packages/pandas/core/dtypes/cast.py:127: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  arr = construct_1d_object_array_from_listlike(values)


In [28]:
# # Import package
# from gtfs_functions import Feed, map_gdf

# feed = Feed("../src/data/gtfs_2024-01-15_2024-01-31.zip")

# routes = feed.routes
# trips = feed.trips
# stops = feed.stops
# stop_times = feed.stop_times
# shapes = feed.shapes

In [9]:
import basedosdados as bd
from zipfile import ZipFile
import pandas as pd
import geopandas as gpd

# Seta o projeto a ser cobrado
bd.config.billing_project_id = "rj-smtr-dev"

In [4]:
with ZipFile("gtfs_combi_2023-12-02Q.zip") as myzip:
    shapes_df = pd.read_csv(myzip.open("shapes.txt"))

    shapes_df = pd.read_csv(myzip.open("shapes.txt"), dtype={
            'shape_id': 'str', 
            'shape_pt_lat': 'float', 
            'shape_pt_lon': 'float',  
            'shape_pt_sequence': 'Int64', 
            'shape_dist_traveled': 'float',
        })

shapes_gdf = gpd.GeoDataFrame(
    shapes_df, 
    geometry=gpd.points_from_xy(shapes_df.shape_pt_lon, shapes_df.shape_pt_lat)
).set_crs(epsg=4326)

In [6]:
shapes_gdf.head()

shape_id  shape_pt_sequence  shape_pt_lat  shape_pt_lon  \
0     01gk                  1     -22.87638     -43.46371   
1     01gk                  2     -22.87553     -43.46372   
2     01gk                  3     -22.87556     -43.46543   
3     01gk                  4     -22.87567     -43.46973   
4     01gk                  5     -22.87570     -43.47027   

   shape_dist_traveled                     geometry  
0                 0.00  POINT (-43.46371 -22.87638)  
1                94.52  POINT (-43.46372 -22.87553)  
2               269.74  POINT (-43.46543 -22.87556)  
3               710.45  POINT (-43.46973 -22.87567)  
4               765.87  POINT (-43.47027 -22.87570)

In [13]:
shapes = bd.read_sql("""
SELECT
  *
FROM
  `rj-smtr.br_rj_riodejaneiro_gtfs.shapes_geom`
WHERE
    data_versao = "2023-12-21"
""")

shapes.info()

Downloading: 100%|███████████████████████████████████████████████████████████████████████████████| 974/974 [00:09<00:00, 99.47rows/s]

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 974 entries, 0 to 973
Data columns (total 7 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   data_versao     974 non-null    dbdate 
 1   shape_id        974 non-null    object 
 2   shape           974 non-null    object 
 3   shape_distance  974 non-null    float64
 4   start_pt        974 non-null    object 
 5   end_pt          974 non-null    object 
 6   versao_modelo   974 non-null    object 
dtypes: dbdate(1), float64(1), object(5)
memory usage: 53.4+ KB


In [26]:
shapes.head()

data_versao         shape_id  \
0  2023-12-21             hj1m   
1  2023-12-21             bjdi   
2  2023-12-21             i768   
3  2023-12-21             6dzv   
4  2023-12-21  O0809AAA0AVDU01   

                                               shape  shape_distance  \
0  MULTILINESTRING((-43.31258 -23.0066, -43.31258...          6277.5   
1  MULTILINESTRING((-43.17441 -22.96503, -43.1743...         31829.4   
2  MULTILINESTRING((-43.17441 -22.96503, -43.1743...         33479.3   
3  MULTILINESTRING((-43.17403 -22.90711, -43.1749...         24986.6   
4  LINESTRING(-43.68531 -22.91527, -43.68566 -22....          7796.1   

                     start_pt                      end_pt  \
0   POINT(-43.31258 -23.0066)  POINT(-43.36616 -23.00101)   
1  POINT(-43.17441 -22.96503)  POINT(-43.18088 -22.79079)   
2  POINT(-43.17441 -22.96503)  POINT(-43.18088 -22.79079)   
3  POINT(-43.17403 -22.90711)  POINT(-43.18088 -22.79079)   
4  POINT(-43.68531 -22.91527)  POINT(-43.65611 -22.88679)   

                              versao_modelo  
0  be879d5aefab6f53c6bb207078d666928aa1efc4  
1  be879d5aefab6f53c6bb207078d666928aa1efc4  
2  be879d5aefab6f53c6bb207078d666928aa1efc4  
3  be879d5aefab6f53c6bb207078d666928aa1efc4  
4  be879d5aefab6f53c6bb207078d666928aa1efc4

In [39]:
shapes_gdf[

4
data_versao                                            2023-12-21
shape_id                                          O0809AAA0AVDU01
shape           LINESTRING(-43.68531 -22.91527, -43.68566 -22....
shape_distance                                             7796.1
start_pt                               POINT(-43.68531 -22.91527)
end_pt                                 POINT(-43.65611 -22.88679)
versao_modelo            be879d5aefab6f53c6bb207078d666928aa1efc4

In [43]:
from shapely.wkt import loads

shapes_gdf = gpd.GeoDataFrame(shapes)
shapes_gdf.shape =  shapes_gdf['shape'].apply(loads)

shapes_gdf.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 974 entries, 0 to 973
Data columns (total 7 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   data_versao     974 non-null    dbdate 
 1   shape_id        974 non-null    object 
 2   shape           974 non-null    object 
 3   shape_distance  974 non-null    float64
 4   start_pt        974 non-null    object 
 5   end_pt          974 non-null    object 
 6   versao_modelo   974 non-null    object 
dtypes: dbdate(1), float64(1), object(5)
memory usage: 53.4+ KB


In [47]:
! pip install gtfs_functions


[notice] A new release of pip is available: 23.2.1 -> 23.3.2
[notice] To update, run: pip install --upgrade pip


In [ ]:
from gtfs_functions import Feed, map_gdf



In [11]:
# gps = bd.read_sql("""
# SELECT
#   timestamp_gps,
#   ordem as id_veiculo,
#   linha as servico,
#   latitude,
#   longitude
# FROM
#   `rj-smtr.br_rj_riodejaneiro_onibus_gps.registros`
# WHERE
#   DATA = CURRENT_DATE("America/Sao_Paulo")
#   AND timestamp_gps >= DATETIME_SUB(CURRENT_DATETIME("America/Sao_Paulo"), INTERVAL 15 minute)
# """)

gps = bd.read_sql("""
SELECT
  count(*)
FROM
  `rj-smtr.br_rj_riodejaneiro_veiculos.gps_brt`
""")

gps.info()

Downloading: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00,  2.41rows/s]

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1 entries, 0 to 0
Data columns (total 1 columns):
 #   Column  Non-Null Count  Dtype
---  ------  --------------  -----
 0   f0_     1 non-null      Int64
dtypes: Int64(1)
memory usage: 137.0 bytes
